# Nella celle seguenti sono creati i dataframe che successivamente verranno utilizzati dal Dataset Pythorc 

In [1]:
import os
import pandas as pd
import numpy as np

data_paths = [
    ("/kaggle/input/meccano/MECCANO_hands_bounding_box_annotations/MECCANO_hands_bounding_box_annotations/Train/", "Train"),
    ("/kaggle/input/meccano/MECCANO_hands_bounding_box_annotations/MECCANO_hands_bounding_box_annotations/Test/", "Test"),
    ("/kaggle/input/meccano/MECCANO_hands_bounding_box_annotations/MECCANO_hands_bounding_box_annotations/Val/", "Val")
]

for input_path, name in data_paths:
    dataset = pd.DataFrame()
    print(input_path)

    for file_name in os.listdir(input_path):
        #print(file_name)
        annotation = pd.read_csv(input_path + file_name)
        n = file_name[:4] + '/'
        #print(n)
        #print("file name annotation : " + annotation['filename'])
        annotation['file_path'] = input_path + n + annotation['filename']
        dataset = pd.concat([dataset, annotation])

    
    dataset['file_path'] = dataset['file_path'].str.replace("/Train/", f"/{name}/")

    dataset.to_csv(f"/kaggle/working/data_{name}.csv", index=False)
print("Processo completato.")


/kaggle/input/meccano/MECCANO_hands_bounding_box_annotations/MECCANO_hands_bounding_box_annotations/Train/
/kaggle/input/meccano/MECCANO_hands_bounding_box_annotations/MECCANO_hands_bounding_box_annotations/Test/
/kaggle/input/meccano/MECCANO_hands_bounding_box_annotations/MECCANO_hands_bounding_box_annotations/Val/
Processo completato.


In [2]:
!pip install pycocotools
from engine import train_one_epoch, evaluate
import utils


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 426.2/426.2 kB 11.7 MB/s eta 0:00:0000:01


Di segiuto vengono eliminati dal dataset i frame che hanno un numero di bounding box  pari a 3 in quanto chiaramente degli errori. 

In [3]:
import json
import pandas as pd
import json

df = pd.read_csv("/kaggle/working/data_Test.csv")


path_list = []
sx_list = []
bboxsx_list = []
dx_list = []
bboxdx_list = []


for index, row in df.iterrows():
    print(row["file_path"])
    path = row["file_path"].replace("MECCANO_hands_bounding_box_annotations/MECCANO_hands_bounding_box_annotations", "MECCANO_RGB_frames/RGB_frames")
    
    region_attributes = json.loads(row["region_attributes"])
    if "class" in region_attributes:
        if region_attributes["class"] == "SX_Hand":
            sx = 1
            box = json.loads(row["region_shape_attributes"])
            bboxsx = [box["x"],box["y"],box["width"],box["height"]]
            #print("bbox")
            #print(bboxsx)
            #dx = 0
            #bboxdx = []
        elif region_attributes["class"] == "DX_Hand":
            dx = 1
            box = json.loads(row["region_shape_attributes"])
            bboxdx = [box["x"],box["y"],box["width"],box["height"]]
            #print("bbox")
            #print(bboxdx)
            #sx = 0
            #bboxsx = []
        else:
            sx = 0
            dx = 0
            bboxsx = []
            bboxdx = []
    else:
        sx = 0
        dx = 0
        bboxsx = []
        bboxdx = []
    
    path_list.append(path)
    sx_list.append(sx)
    bboxsx_list.append(bboxsx)
    dx_list.append(dx)
    bboxdx_list.append(bboxdx)


df["path"] = path_list
df["sx"] = sx_list
df["bboxsx"] = bboxsx_list
df["dx"] = dx_list
df["bboxdx"] = bboxdx_list


df  = df.drop(columns=["filename","region_attributes", "region_shape_attributes","region_count" ,"region_id","file_attributes","file_size" ,"file_path"])


#df.to_csv("/kaggle/working/provaannotazione.csv")
#df["path"].values

df.to_csv("/kaggle/working/data_test_annotated.csv")

/kaggle/input/meccano/MECCANO_hands_bounding_box_annotations/MECCANO_hands_bounding_box_annotations/Test/0019/00078.jpg
/kaggle/input/meccano/MECCANO_hands_bounding_box_annotations/MECCANO_hands_bounding_box_annotations/Test/0019/00079.jpg
/kaggle/input/meccano/MECCANO_hands_bounding_box_annotations/MECCANO_hands_bounding_box_annotations/Test/0019/00080.jpg
/kaggle/input/meccano/MECCANO_hands_bounding_box_annotations/MECCANO_hands_bounding_box_annotations/Test/0019/00081.jpg
/kaggle/input/meccano/MECCANO_hands_bounding_box_annotations/MECCANO_hands_bounding_box_annotations/Test/0019/00082.jpg
/kaggle/input/meccano/MECCANO_hands_bounding_box_annotations/MECCANO_hands_bounding_box_annotations/Test/0019/00083.jpg
/kaggle/input/meccano/MECCANO_hands_bounding_box_annotations/MECCANO_hands_bounding_box_annotations/Test/0019/00084.jpg
/kaggle/input/meccano/MECCANO_hands_bounding_box_annotations/MECCANO_hands_bounding_box_annotations/Test/0019/00084.jpg
/kaggle/input/meccano/MECCANO_hands_boun

In [4]:
import pandas as pd
data = pd.read_csv("/kaggle/working/data_train_annotated.csv")
data_val =  pd.read_csv("/kaggle/working/data_val_annotated.csv")
data_test = pd.read_csv("/kaggle/working/data_test_annotated.csv")
data.head()

Unnamed: 0                                               path  sx bboxsx  \
0           0  /kaggle/input/meccano/MECCANO_RGB_frames/RGB_f...   0     []   
1           1  /kaggle/input/meccano/MECCANO_RGB_frames/RGB_f...   0     []   
2           2  /kaggle/input/meccano/MECCANO_RGB_frames/RGB_f...   0     []   
3           3  /kaggle/input/meccano/MECCANO_RGB_frames/RGB_f...   0     []   
4           4  /kaggle/input/meccano/MECCANO_RGB_frames/RGB_f...   0     []   

   dx bboxdx  
0   0     []  
1   0     []  
2   0     []  
3   0     []  
4   0     []

# Nelle seguente sezione di codice è definito il Dataset Pythorc successivamente utilizzato per l'addestramento delle reti neurali.

In [5]:
from torch.utils.data.dataset import Dataset
import torchvision.transforms as transforms
import torch


from PIL import Image
from os import path

class MyDataset(Dataset):
    
    def __init__(self, data, transform= None):
        self.data = data
        self.transform=transform

    def __len__(self):
        return len(self.data)
    
    def __getitem__(self, index):
        target = {
            "labels" : []
        }
        boxes = []

        image_path = self.data.loc[index, 'path']
        image = (Image.open(image_path).convert('RGB'))
        image = transform(image)
        sx = self.data.loc[index, 'sx']
        dx = self.data.loc[index, 'dx']
        
        num_objs = 0

        if sx == 1:
            bbox_sx = self.data.loc[index, 'bboxsx'].split(",")
            bbox_sx[0] = bbox_sx[0].replace("[", "")
            bbox_sx[3] = bbox_sx[3].replace("]", "")
            bbox_sx = [eval(i) for i in bbox_sx]
            bbox_sx[2]=bbox_sx[0]+bbox_sx[2]
            bbox_sx[3]=bbox_sx[1]+bbox_sx[3]
            
            boxes.append(bbox_sx)
            target["labels"].append(0)
            num_objs+=1
        
        
        if dx == 1:
            bbox_dx = self.data.loc[index, 'bboxdx'].split(",")
            bbox_dx[0] = bbox_dx[0].replace("[", "")
            bbox_dx[3] = bbox_dx[3].replace("]", "")
            bbox_dx = [eval(i) for i in bbox_dx]
            bbox_dx[2]=bbox_dx[0]+bbox_dx[2]
            bbox_dx[3]=bbox_dx[1]+bbox_dx[3]
            
            boxes.append(bbox_dx)
            target["labels"].append(1)
            num_objs+=1
        

        #area = (boxes[:, 3] - boxes[:, 1]) * (boxes[:, 2] - boxes[:, 0])

        if not boxes:
            boxes = torch.as_tensor(boxes, dtype=torch.float32)
            boxes = boxes.reshape(-1, 4)
            #area = torch.as_tensor(boxes, dtype=torch.float32)
            #area = area.reshape(-1,1)
        else :
            boxes = torch.tensor(boxes, dtype=torch.float32)
        target["boxes"] = boxes


        area = (boxes[:, 3] - boxes[:, 1]) * (boxes[:, 2] - boxes[:, 0])
       
        iscrowd = torch.zeros((num_objs,), dtype=torch.int64)
        
        
        target["area"] = area
        #print(area)
        target["iscrowd"] = iscrowd
        target["labels"] = torch.tensor(target["labels"], dtype=torch.int64)
        target["image_id"] = index

        
        return image,target

In [6]:
transform = transforms.Compose([
            transforms.ToTensor()
        ])

### Viene importato il modello fasterrcnn_resnet50_fpn dalle librerie torchvision

In [7]:
import torch
import torchvision

model = torchvision.models.detection.fasterrcnn_resnet50_fpn(pretrained=True)

/opt/conda/lib/python3.10/site-packages/torchvision/models/_utils.py:208: UserWarning: The parameter 'pretrained' is deprecated since 0.13 and may be removed in the future, please use 'weights' instead.
  warnings.warn(
/opt/conda/lib/python3.10/site-packages/torchvision/models/_utils.py:223: UserWarning: Arguments other than a weight enum or `None` for 'weights' are deprecated since 0.13 and may be removed in the future. The current behavior is equivalent to passing `weights=FasterRCNN_ResNet50_FPN_Weights.COCO_V1`. You can also use `weights=FasterRCNN_ResNet50_FPN_Weights.DEFAULT` to get the most up-to-date weights.
  warnings.warn(msg)
Downloading: "https://download.pytorch.org/models/fasterrcnn_resnet50_fpn_coco-258fb6c6.pth" to /root/.cache/torch/hub/checkpoints/fasterrcnn_resnet50_fpn_coco-258fb6c6.pth
100%|██████████| 160M/160M [00:01<00:00, 90.3MB/s] 


In [8]:
model.state_dict

<bound method Module.state_dict of FasterRCNN(
  (transform): GeneralizedRCNNTransform(
      Normalize(mean=[0.485, 0.456, 0.406], std=[0.229, 0.224, 0.225])
      Resize(min_size=(800,), max_size=1333, mode='bilinear')
  )
  (backbone): BackboneWithFPN(
    (body): IntermediateLayerGetter(
      (conv1): Conv2d(3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False)
      (bn1): FrozenBatchNorm2d(64, eps=0.0)
      (relu): ReLU(inplace=True)
      (maxpool): MaxPool2d(kernel_size=3, stride=2, padding=1, dilation=1, ceil_mode=False)
      (layer1): Sequential(
        (0): Bottleneck(
          (conv1): Conv2d(64, 64, kernel_size=(1, 1), stride=(1, 1), bias=False)
          (bn1): FrozenBatchNorm2d(64, eps=0.0)
          (conv2): Conv2d(64, 64, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
          (bn2): FrozenBatchNorm2d(64, eps=0.0)
          (conv3): Conv2d(64, 256, kernel_size=(1, 1), stride=(1, 1), bias=False)
          (bn3): FrozenBatchNorm2d(25

#### il layer di classificazione del modello viene modificato in maniera da predire due classi (mano sinistra e mano destra). Il layer di regressione viene modificato in maniera tale da predire se presenti le coordinate dei bounding box.

In [10]:
model.roi_heads.box_predictor.cls_score = torch.nn.Linear(in_features=1024, out_features=2, bias=True)
model.roi_heads.box_predictor.bbox_pred = torch.nn.Linear(in_features=1024, out_features=8, bias=True)

In [11]:
def collate_fn(batch):
    return tuple(zip(*batch))

In [12]:
data = data.sample(frac=1).reset_index(drop=True)
data_val = data_val.sample(frac=1).reset_index(drop=True)

#### successivamente sono definiti i dataloader necessari per l'addestramento, optimizer e scheluder e qualora fosse possibile il modello viene traslato su GPU. 

In [13]:
data_train = MyDataset(data,transform)
pt_dataset_val = MyDataset(data_val,transform)

data_loader = torch.utils.data.DataLoader(data_train,batch_size=4,num_workers=2,collate_fn=collate_fn)
data_loader_validation = torch.utils.data.DataLoader(pt_dataset_val,batch_size=4,num_workers=2,collate_fn=collate_fn)
device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')
print(device)
model.to(device)

params = [p for p in model.parameters() if p.requires_grad]


optimizer = torch.optim.SGD(params, lr=0.005,momentum=0.9, weight_decay=0.0005)

lr_scheduler = torch.optim.lr_scheduler.StepLR(optimizer,step_size=3,gamma=0.1)

cuda


In [14]:
!pip install wandb

In [15]:
!wandb login a242e5dc3fed798efc0e8b17e501b8220116ca73


wandb: WARNING If you're specifying your api key in code, ensure this code is not shared publicly.
wandb: WARNING Consider setting the WANDB_API_KEY environment variable, or running `wandb login` from the command line.
wandb: Appending key for api.wandb.ai to your netrc file: /root/.netrc


In [16]:
import wandb
def log_init(lr, batch_size,epochs):

    wandb.init(
        project="progettoML2",
        name="Fastercnn_resnet50_fpn",
        config={

            "learning_rate": lr,

            "batch_size":batch_size,

            "architecture": "Fastercnn_resnet50_fpn",

            "epochs": epochs,

        },resume = True)
    

redirezione dello standard output di python al fine di salvare successivamene le prestazioni ottenute.

In [17]:
import sys
val = sys.__stdout__

#### Nella cella di seguito viene effettuato il training della rete neurale, caricando dei checkpoint se presenti. Il modello per ogni epoca viene anche valutato sul validation e i log sono analizzati tramite WandB.

In [ ]:
import io
import sys
import re
from torch.optim.lr_scheduler import StepLR


loss_pattern = r"loss: ([\d.]+) \([\d.]+\)"


output_buffer = io.StringIO()
sys.stdout = output_buffer

num_epochs = 0
model.load_state_dict(torch.load("./checkpoint.pth"))

TOT_EPOCH = 50
CHECKPOINT_PATH = "./checkpoint.pth"


run = log_init(0.005,4,num_epochs)

'''
if wandb.run.resumed:
    
    checkpoint = torch.load(wandb.restore(CHECKPOINT_PATH))
    model.load_state_dict(checkpoint['model_state_dict'])
    optimizer.load_state_dict(checkpoint['optimizer_state_dict'])
    num_epochs = checkpoint['epoch']
    loss = checkpoint['loss']
'''

epoch_losses = []


while num_epochs <= TOT_EPOCH:
    output_buffer = io.StringIO()
    sys.stdout = output_buffer
    epoch_losses = []
# alleniamo per un'epoca e stampiamo il log ogni 10 iterazioni
    var = train_one_epoch(model, optimizer, data_loader, device, num_epochs, print_freq=10)
    
    #print(var.meters["loss"].value)

    lr_scheduler.step()
# valutiamo sul test set
   
    sys.stdout = val
    captured_output = output_buffer.getvalue()
    
    loss_values = re.findall(loss_pattern, captured_output)
    epoch_losses = [float(val) for val in loss_values]
    
    last_loss = 0
    for loss in epoch_losses:
        last_loss = loss
        wandb.log({"loss/training": loss})
    
    value = evaluate(model, data_loader, device=device)
    ap_arr = value.coco_eval["bbox"].stats
    wandb.log({"AP@IoU0.50:0.95/training": ap_arr[0],
               "AP@IoU0.50/training": ap_arr[1],
               "AP@IoU0.75/training": ap_arr[2],
               "AR@IoU0.50:0.95@max_dets=1/training": ap_arr[6],
               "AR@IoU0.50:0.95@max_dets=100/training": ap_arr[8]})
    
    value = evaluate(model, data_loader_validation, device=device)
    ap_arr = value.coco_eval["bbox"].stats
    wandb.log({"AP@IoU0.50:0.95/validation": ap_arr[0],
               "AP@IoU0.50/validation": ap_arr[1],
               "AP@IoU0.75/validation": ap_arr[2],
               "AR@IoU0.50:0.95@max_dets=1/validation": ap_arr[6],
               "AR@IoU0.50:0.95@max_dets=100/validation": ap_arr[8],
               "epoca" : num_epochs})
    
    
    torch.save(model.state_dict(),CHECKPOINT_PATH)
    #wandb.save(CHECKPOINT_PATH)
    
    
    num_epochs+=1
    
    
empty_output = io.StringIO()

# Redirigi stdout verso l'oggetto StringIO vuoto
sys.stdout = empty_output

# Stampa l'output catturato
#print(captured_output)


### Di seguito viene caricato il modello migliore ottenuto sul validation e testato sul test set  

In [18]:
model.load_state_dict(torch.load("./checkpoint.pth"))

pt_dataset_test = MyDataset(data_test,transform)

data_loader_test = torch.utils.data.DataLoader(pt_dataset_test,batch_size=4,num_workers=2,collate_fn=collate_fn)

In [20]:
import io
import sys
import re
from torch.optim.lr_scheduler import StepLR


model.eval()

value = evaluate(model, data_loader_test, device=device)
ap_arr = value.coco_eval["bbox"].stats


wandb.log({"AP@IoU0.50:0.95/test": ap_arr[0],
               "AP@IoU0.50/test": ap_arr[1],
               "AP@IoU0.75/test": ap_arr[2],
               "AR@IoU0.50:0.95@max_dets=1/test": ap_arr[6],
               "AR@IoU0.50:0.95@max_dets=100/test": ap_arr[8]})


creating index...
index created!
Test:  [    0/13439]  eta: 18:54:12  model_time: 4.5778 (4.5778)  evaluator_time: 0.0297 (0.0297)  time: 5.0638  data: 0.4172  max mem: 1875
Test:  [  100/13439]  eta: 1:23:47  model_time: 0.2534 (0.2964)  evaluator_time: 0.0198 (0.0208)  time: 0.3296  data: 0.0279  max mem: 1883
Test:  [  200/13439]  eta: 1:18:36  model_time: 0.2546 (0.2755)  evaluator_time: 0.0207 (0.0207)  time: 0.3345  data: 0.0280  max mem: 1883
Test:  [  300/13439]  eta: 1:16:01  model_time: 0.2536 (0.2684)  evaluator_time: 0.0193 (0.0205)  time: 0.3279  data: 0.0261  max mem: 1883
Test:  [  400/13439]  eta: 1:14:30  model_time: 0.2541 (0.2649)  evaluator_time: 0.0192 (0.0204)  time: 0.3277  data: 0.0264  max mem: 1883
Test:  [  500/13439]  eta: 1:13:25  model_time: 0.2554 (0.2630)  evaluator_time: 0.0200 (0.0204)  time: 0.3307  data: 0.0266  max mem: 1883
Test:  [  600/13439]  eta: 1:12:31  model_time: 0.2554 (0.2619)  evaluator_time: 0.0190 (0.0204)  time: 0.3295  data: 0.0267 